# Visualize the Data

In [1]:
import pandas as pd
from pandas_profiling import ProfileReport

# import local scripts
import sys,os
os.chdir("..")
sys.path.append(os.getcwd())
from preprocessor.paths import (PATH_TO_PLANT_A, PATH_TO_WEATHER)
from preprocessor.preprocessor import Preprocessor

The history saving thread hit an unexpected error (DatabaseError('database disk image is malformed')).History will not be written to the database.


## Data Preparation

In [2]:
# use UTC timestamps

data_power_plant = Preprocessor(PATH_TO_PLANT_A, local_time_column="timestamp", resampling_method="sum").df_indexed_utc
data_weather = Preprocessor(PATH_TO_WEATHER, local_time_column="local_time", resampling_method="mean").df_indexed_utc

In [3]:
# combine dataframes for plots
data = data_power_plant.merge(data_weather,
                              left_index=True, 
                              right_index=True)

In [4]:
# copy last the row so we have a full year of data.
# this is necessary, because the timestamps (observations) of the weather dataset
# begins one hour later than the observations of the power plant dataset.
# the combination of the dataframes in the previous step thus resulted in one missing hour.
# we will copy data from around midnight for the last row,
# when the sun is not shining, so this will be unproblematic.

last_index = data.index[-1]
new_last_index = last_index + pd.Timedelta('1 hour')
data.loc[new_last_index] = data.loc[last_index]

## Data Exploration

In [5]:
profile = ProfileReport(data, title="Pandas Profiling Report")
profile.to_notebook_iframe()